<a href="https://colab.research.google.com/github/kidrono/DSSG-Chromatography/blob/master/easy_to_use_code.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from scipy.spatial.distance import pdist,squareform
from scipy.cluster.hierarchy import linkage,fcluster


def dis(df_only_index,threshold):
  #this function gets a data frame that contains places of the peaks 
  #and returns clusters of them by distance 
  D=squareform(pdist(df_only_index))
  disMat = squareform(D)
  Z = linkage(disMat,method='complete')
  cluster= fcluster(Z, threshold, 'distance')
  cluster_assignments = [np.where(cluster==k)[0] for k in np.unique(cluster)]
  return cluster_assignments


def create_title(document,number_in_table,title):
  df = pd.read_csv(document)
  address=df.loc[[number_in_table]]['sample'].values[0]
  full_adress="/content/drive/My Drive/"+address+"tic_front.csv"
  sample=pd.read_csv(full_adress,names=['x','y']).iloc[1:]
  title_=title + " " + address
  sample.plot(x='x', y='y', title=title_)
  

def choose_col(num_of_peaks,index_or_value):
  #this function returns a least of colums to check over 
  arr=[]
  for i in range(1,num_of_peaks+1):
    arr.append('peak_'+str(i)+'_'+index_or_value)
  return arr

def scale_data(df):
  #this function normalize by highest peak and after that replace the cols with it 
  for col in df.columns:
    df[col] = absolute_maximum_scale(df[col])
  return df


def absolute_maximum_scale(series):
    return series / series.max()


def list_to_df(samples_list):
    clusters_of_samples = []
    for cluster_num in range(len(samples_list)):
        for sample in samples_list[cluster_num]:
            clusters_of_samples.append((sample, cluster_num))
    clusters = []
    samples = []
    for pair in clusters_of_samples:
        samples.append(pair[0])
        clusters.append(pair[1])
    new_df = pd.DataFrame()
    new_df['sample'] = samples
    new_df['cluster'] = clusters
    return new_df



def make_clusters_per_peak(document,num_of_peaks,thershold_for_time,thershold_for_ratio,to_create_plot=False):
  #this funcion gets a documents of a all samples of a methods, and num of peaks 
  #to check, and returns the clusters  
  print()
  arr_of_cluster=[]
  df = pd.read_csv(document)
  df = df[df['num_of_peaks'] ==num_of_peaks]
  df = df.drop([col for col in df.columns if df[col].eq(-1).any()], axis=1)

  only_peaks_location = df[choose_col(num_of_peaks,'index')]
  cluster_assignments = dis(only_peaks_location,thershold_for_time)
  num_clusters =0
  for cluster in range(len(cluster_assignments)):

    if (cluster_assignments[cluster].shape[0]>1):
      in_cluster=df.loc[only_peaks_location.iloc[cluster_assignments[cluster]].index.values]
      in_cluster_only_peaks=in_cluster[choose_col(num_of_peaks,'value')].transpose()
      in_cluster_only_peaks_norm=scale_data(in_cluster_only_peaks).transpose()
      cluster_assignments_in_cluster=dis(in_cluster_only_peaks_norm,thershold_for_ratio)
      for sub_clust in range(len(cluster_assignments_in_cluster)):
          num_clusters=num_clusters+1
          first= in_cluster_only_peaks_norm.iloc[cluster_assignments_in_cluster[sub_clust]].index
          sub_arr=[]
          for i in first:
            if to_create_plot:
              create_title(document,i, str(cluster)+" "+str(sub_clust) )
            sub_arr.append(df.loc[[i]]['sample'].values[0])
          arr_of_cluster.append(sub_arr)

    else:
      pass
      # print(df.loc[only_peaks_location.iloc[cluster_assignments[cluster]].index.values])
      if to_create_plot:
        create_title(document,df.loc[only_peaks_location.iloc[cluster_assignments[cluster]].index.values].index[0],"Alone")
      lonley_arr=[]
      lonley_arr.append(df.loc[only_peaks_location.iloc[cluster_assignments[cluster]].index.values]['sample'].values[0])
      arr_of_cluster.append(lonley_arr)
  count=0
  for elm in arr_of_cluster:
    count += len(elm)
  return list_to_df(arr_of_cluster)


  
  



all_clusters_per_peak=make_clusters_per_peak("drug_auto_updated_new.csv",2,0.1,0.025)
# all_clusters_per_peak.to_csv("drug_auto_updated_2_peaks_new.csv")



In [ ]:




import scipy as sci
sci.__version__


'1.7.3'

In [ ]:
from ipywidgets import interact, interactive, fixed, interact_manual

def choose_thresholds(distance,ratio):
  make_clusters_per_peak("drug_auto_updated_new.csv",2,distance,ratio,True)

interact(choose_thresholds, distance=(0.01, 1, 0.02),ratio=(0.01, 1, 0.002));

interactive(children=(FloatSlider(value=0.49, description='distance', max=1.0, min=0.01, step=0.02), FloatSlid…

In [ ]:
from google.colab import drive 

#this section mounts all drive folders into the colab
drive.mount('/content/drive')

Mounted at /content/drive
